In [4]:
import pandas as pd
import numpy as np

import seaborn as sns
import matplotlib.pyplot as plt

import os

from transformers import pipeline

import requests
import json
import openai

from medisure.ml_logic.data import clean_text, eda_pipeline
from medisure.ml_logic.FDI import get_tau_score
from medisure.ml_logic.DDI import ddi_data


[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/raynasser/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/raynasser/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /Users/raynasser/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [3]:
base_path = '/Users/raynasser/code/raynasser/MediSure/data/raw_data'
foodrug = '/Users/raynasser/code/raynasser/MediSure/data/raw_data/FooDru'
ddi = '/Users/raynasser/code/raynasser/MediSure/data/raw_data/drugs_allergic_interaction'

In [48]:
files = [f for f in os.listdir(base_path) if f.endswith('.csv')]
files

['medicine_dataset.csv',
 'PubChemLite_31Oct2020_exposomics.csv',
 'Allergen_Status_of_Food_Products.csv',
 'drug_relation_dfe.csv',
 'Medicine.csv']

In [49]:
medicine_dataset = pd.read_csv(os.path.join(base_path, 'medicine_dataset.csv'), index_col='id')
medicine_dataset

/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_19659/1606911670.py:1: DtypeWarning: Columns (42,43,44,45,46,47,48) have mixed types. Specify dtype option on import or set low_memory=False.
  medicine_dataset = pd.read_csv(os.path.join(base_path, 'medicine_dataset.csv'), index_col='id')


name  \
id                                             
1                   augmentin 625 duo tablet   
2                        azithral 500 tablet   
3                           ascoril ls syrup   
4                       allegra 120mg tablet   
5                             avil 25 tablet   
...                                      ...   
248214  zestrain 100mg/325mg/250mg tablet mr   
248215              zoxinace 200mg tablet sr   
248216                     zivex 25mg tablet   
248217               zi fast 500mg injection   
248218             zyvocol 1% dusting powder   

                                substitute0             substitute1  \
id                                                                    
1            Penciclav 500 mg/125 mg Tablet  Moxikind-CV 625 Tablet   
2                   Zithrocare 500mg Tablet         Azax 500 Tablet   
3                           Solvin LS Syrup       Ambrodil-LX Syrup   
4                              Lcfex Tablet     Etofex 120mg Tablet   
5                        Eralet 25mg Tablet                     NaN   
...                                     ...                     ...   
248214  Aclotec MR 100mg/325mg/250mg Tablet       SAMONEC MR TABLET   
248215                Algic 200mg Tablet SR  Topnac 200mg Tablet SR   
248216                  HD Zine 25mg Tablet    Hydrocas 25mg Tablet   
248217                Zycin 500mg Injection  Aziwok 500mg Injection   
248218              Canazole Dusting Powder  Clotrex Dusting Powder   

                                substitute2  \
id                                            
1                   Moxiforce-CV 625 Tablet   
2                           Zady 500 Tablet   
3                         Zerotuss XP Syrup   
4                      Nexofex 120mg Tablet   
5                                       NaN   
...                                     ...   
248214  Uniclof 100mg/325mg/250mg Tablet MR   
248215               Kindac 200mg Tablet SR   
248216                      Hyzox 25 Tablet   
248217               Azirow 500mg Injection   
248218                 AF -C Dusting Powder   

                               substitute3  \
id                                           
1                       Fightox 625 Tablet   
2                    Cazithro 500mg Tablet   
3                           Capex LS Syrup   
4                      Fexise 120mg Tablet   
5                                      NaN   
...                                    ...   
248214  Macito 100mg/325mg/250mg Tablet MR   
248215            Ultranac 200mg Tablet SR   
248216                   Hydil 25mg Tablet   
248217             Toracin 500mg Injection   
248218              Klo-Aid Dusting Powder   

                                substitute4  \
id                                            
1                   Novamox CV 625mg Tablet   
2                     Trulimax 500mg Tablet   
3                           Broxum LS Syrup   
4                      Histafree 120 Tablet   
5                                       NaN   
...                                     ...   
248214  Rumatin 100mg/325mg/250mg Tablet MR   
248215               Bignac 200mg Tablet SR   
248216                   Zyzine 25mg Tablet   
248217               Azymed 500mg Injection   
248218               Nuforce Dusting Powder   

                                              sideEffect0       sideEffect1  \
id                                                                            
1                                                Vomiting            Nausea   
2                                                Vomiting            Nausea   
3                                                  Nausea          Vomiting   
4                                                Headache        Drowsiness   
5                                              Sleepiness  Dryness in mouth   
...                                                   ...               ...   
248214                              

In [50]:
eda_pipeline(medicine_dataset)

_________________________________


Columns:
Index(['name', 'substitute0', 'substitute1', 'substitute2', 'substitute3',
       'substitute4', 'sideEffect0', 'sideEffect1', 'sideEffect2',
       'sideEffect3', 'sideEffect4', 'sideEffect5', 'sideEffect6',
       'sideEffect7', 'sideEffect8', 'sideEffect9', 'sideEffect10',
       'sideEffect11', 'sideEffect12', 'sideEffect13', 'sideEffect14',
       'sideEffect15', 'sideEffect16', 'sideEffect17', 'sideEffect18',
       'sideEffect19', 'sideEffect20', 'sideEffect21', 'sideEffect22',
       'sideEffect23', 'sideEffect24', 'sideEffect25', 'sideEffect26',
       'sideEffect27', 'sideEffect28', 'sideEffect29', 'sideEffect30',
       'sideEffect31', 'sideEffect32', 'sideEffect33', 'sideEffect34',
       'sideEffect35', 'sideEffect36', 'sideEffect37', 'sideEffect38',
       'sideEffect39', 'sideEffect40', 'sideEffect41', 'use0', 'use1', 'use2',
       'use3', 'use4', 'Chemical Class', 'Habit Forming', 'Therapeutic Class',
       'Action Class'],

TypeError: readline.redisplay() takes no arguments (1 given)

In [155]:
def lower(text):
    try:
        return text.lower()
    except:
        return text





# def summarize(text):
#     pipe = pipeline('summarization', model= 'sshleifer/distilbart-xsum-12-6')

#     summary = pipe(text)
#     return summary[0]['summary_text']
#     # return pipe(text)







def clasic(text):

    pipe = pipeline('question-answering', model= 'deepset/roberta-base-squad2')

    return pipe(question = 'Decribe the interaction between food and the drug here?',context=text)

In [8]:
files = [f for f in os.listdir(foodrug) if f.endswith('.csv')]
files

['unique_foods.csv',
 'misc_sample.csv',
 'nodes.csv',
 'texts.csv',
 'unique_drugs.csv',
 'sample.csv',
 'cmap.csv',
 'cmap_foodrugs.csv',
 'misc_study.csv',
 'TM_interactions.csv',
 'study.csv',
 'topTable.csv']

In [9]:
# df8 = pd.read_csv('/Users/raynasser/Downloads/DSproj/FooDru/TM_interactions.csv', index_col='Unnamed: 0')
# df8

foodrug_TM_interactions = pd.read_csv(os.path.join(foodrug, 'TM_interactions.csv'), index_col='Unnamed: 0')
# foodrug_TM_interactions.drop(columns= ['link', 'citation'], inplace=True)
foodrug_TM_interactions



foodrug_texts = pd.read_csv(os.path.join(foodrug, 'texts.csv'), index_col='Unnamed: 0')
foodrug_texts.drop(columns= ['link', 'citation'], inplace=True)
foodrug_texts

/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_19659/2647824967.py:4: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  foodrug_TM_interactions = pd.read_csv(os.path.join(foodrug, 'TM_interactions.csv'), index_col='Unnamed: 0')


texts_ID                                           document
0            0  Moderate Food Interaction||GENERALLY AVOID:  G...
1            2  Major Food Interaction||GENERALLY AVOID:  Alco...
2            7  Moderate Food Interaction||MONITOR:  Coadminis...
3           11  Moderate Drug Interaction||GENERALLY AVOID:  E...
4           13  Moderate Drug Interaction||GENERALLY AVOID:  T...
...        ...                                                ...
8346      8441  The Use of a Continuous Glucose Monitoring Sys...
8347      8442  Glycemic Optimization On Discharge From the Em...
8348      8443  PANDA: PKU Amino Acid Evaluation Phenylketonur...
8349      8444  SNAP: Study Nutrients in Adult PKU Phenylketon...
8350      8445  Effects of Tibilone on Bone Density, Menopause...

[8351 rows x 2 columns]

In [10]:
fdi_pre = foodrug_texts.merge(foodrug_TM_interactions,on="texts_ID")#.drop(columns=["link","citation"])
fdi_pre

texts_ID                                           document  \
0             0  Moderate Food Interaction||GENERALLY AVOID:  G...   
1             0  Moderate Food Interaction||GENERALLY AVOID:  G...   
2             0  Moderate Food Interaction||GENERALLY AVOID:  G...   
3             2  Major Food Interaction||GENERALLY AVOID:  Alco...   
4             2  Major Food Interaction||GENERALLY AVOID:  Alco...   
...         ...                                                ...   
15021      8443  PANDA: PKU Amino Acid Evaluation Phenylketonur...   
15022      8443  PANDA: PKU Amino Acid Evaluation Phenylketonur...   
15023      8444  SNAP: Study Nutrients in Adult PKU Phenylketon...   
15024      8444  SNAP: Study Nutrients in Adult PKU Phenylketon...   
15025      8445  Effects of Tibilone on Bone Density, Menopause...   

       TM_interactions_ID  start_index  end_index                      food  \
0                     0.0          0.0      116.0                Grapefruit   
1                     1.0       1943.0     2220.0              carbohydrate   
2                     2.0       2289.0     2392.0                grapefruit   
3                     3.0        385.0      641.0                grapefruit   
4                     4.0        643.0      846.0                grapefruit   
...                   ...          ...        ...                       ...   
15021             15064.0          0.0      268.0             phenylalanine   
15022             15065.0        269.0      434.0                      diet   
15023             15066.0          0.0      270.0             phenylalanine   
15024             15067.0        271.0      436.0                      diet   
15025             15068.0          0.0      365.0  17alpha-ethynylestradiol   

                  drug  
0          abemaciclib  
1          abemaciclib  
2          abemaciclib  
3             fentanyl  
4             fentanyl  
...                ...  
15021    Phenylalanine  
15022  Phenylketonuria  
15023    Phenylalanine  
15024  Phenylketonuria  
15025         tibolone  

[15026 rows x 7 columns]

In [11]:
fdi_pre["food"] = fdi_pre.food.map(lower)
fdi_pre["drug"] = fdi_pre.drug.map(lower)

In [12]:
fdi_pre

texts_ID                                           document  \
0             0  Moderate Food Interaction||GENERALLY AVOID:  G...   
1             0  Moderate Food Interaction||GENERALLY AVOID:  G...   
2             0  Moderate Food Interaction||GENERALLY AVOID:  G...   
3             2  Major Food Interaction||GENERALLY AVOID:  Alco...   
4             2  Major Food Interaction||GENERALLY AVOID:  Alco...   
...         ...                                                ...   
15021      8443  PANDA: PKU Amino Acid Evaluation Phenylketonur...   
15022      8443  PANDA: PKU Amino Acid Evaluation Phenylketonur...   
15023      8444  SNAP: Study Nutrients in Adult PKU Phenylketon...   
15024      8444  SNAP: Study Nutrients in Adult PKU Phenylketon...   
15025      8445  Effects of Tibilone on Bone Density, Menopause...   

       TM_interactions_ID  start_index  end_index                      food  \
0                     0.0          0.0      116.0                grapefruit   
1                     1.0       1943.0     2220.0              carbohydrate   
2                     2.0       2289.0     2392.0                grapefruit   
3                     3.0        385.0      641.0                grapefruit   
4                     4.0        643.0      846.0                grapefruit   
...                   ...          ...        ...                       ...   
15021             15064.0          0.0      268.0             phenylalanine   
15022             15065.0        269.0      434.0                      diet   
15023             15066.0          0.0      270.0             phenylalanine   
15024             15067.0        271.0      436.0                      diet   
15025             15068.0          0.0      365.0  17alpha-ethynylestradiol   

                  drug  
0          abemaciclib  
1          abemaciclib  
2          abemaciclib  
3             fentanyl  
4             fentanyl  
...                ...  
15021    phenylalanine  
15022  phenylketonuria  
15023    phenylalanine  
15024  phenylketonuria  
15025         tibolone  

[15026 rows x 7 columns]

In [13]:
# summ_ =foodrug_texts.merge(foodrug_TM_interactions,on="texts_ID").tail(50).apply(lambda x: x["document"][int(x["start_index"]):int(x["end_index"])], axis=1).map(summarize)

summ_ =fdi_pre.head(5).apply(lambda x: x["document"][int(x["start_index"]):int(x["end_index"])], axis=1).map(summarize)

Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Your max_length is set to 62, but your input_length is only 30. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=15)
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Your max_length is set to 62, but your input_length is only 22. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=11)
Hardware accelerator e.g. GPU is available in the environment, but

In [14]:
summ_

0     Grapefruit juice may increase the concentrati...
1     A high-calorie meal increases the activity of...
2     A new treatment for bowel cancer has been app...
3     A small quantity of grapefruit juice can be u...
4     A study has suggested grapefruit may be a pot...
dtype: object

In [15]:
# for i in range(0, 5):
#     print(summ_[i][0]["summary_text"])

In [16]:
fdi_pre["clean_text"] = fdi_pre.apply(lambda x: x["document"][int(x["start_index"]):int(x["end_index"])], axis=1)

In [17]:
# fdi_pre['summarized_text'] = summ_[i][0]["summary_text"]

fdi_combo = fdi_pre.groupby(by="texts_ID").agg({"food":lambda x: x.mode()[0],"drug":lambda x: x.mode()[0],"clean_text":lambda x: '. '.join(x)}).reset_index()

In [18]:
fdi_combo.head(5)

texts_ID        food               drug  \
0         0  grapefruit        abemaciclib   
1         2  grapefruit           fentanyl   
2         7  grapefruit         paclitaxel   
3        11     ethanol  opioid analgesics   
4        13     ethanol   dextromethorphan   

                                          clean_text  
0  Moderate Food Interaction||GENERALLY AVOID:  G...  
1  GENERALLY AVOID:  Consumption of grapefruit ju...  
2  Moderate Food Interaction||MONITOR:  Coadminis...  
3  Moderate Drug Interaction||GENERALLY AVOID:  E...  
4  Moderate Drug Interaction||GENERALLY AVOID:  T...

In [19]:
fdi_combo.shape

(8272, 4)

In [20]:
# summ_ = fdi_combo.head(5).clean_text.map(summarize)

In [21]:
# for i in range(5):
#     print(summ_[i][0]["summary_text"])

In [22]:
# fdi_combo["summarize"] = fdi_combo.clean_text.map(summarize)

fdi_map = fdi_combo.head(5)
fdi_map["summarize"] = fdi_map.clean_text.map(summarize)

Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_19659/2695138707.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: h

In [23]:
fdi_map.iloc[3]

texts_ID                                                     11
food                                                    ethanol
drug                                          opioid analgesics
clean_text    Moderate Drug Interaction||GENERALLY AVOID:  E...
summarize      Ethanol can be used as a treatment for painki...
Name: 3, dtype: object

In [24]:


def tau_score(text):

    # Define the API key and endpoint
    API_KEY = os.environ.get("API_KEY")


    # Set up headers for the API request
    client = openai.OpenAI(api_key=API_KEY)


    # run = client.beta.threads.runs.create(
    # thread_id="thread_1LsGTC2QCPTf1AU0S1fVMvZW",
    # assistant_id="asst_fjluyXIaT4Q7tNQ3nJrybazU",
    # additional_instructions=text
    # #extra_query=text
    # )


    completion = client.chat.completions.create(
    model="gpt-4o",
    messages=[
        {"role": "assistant", "content": """You are tasked with elevating interaction between food and drugs fron a summary from a study document.
Analyze and identify the food and the drug in the text and the kind of relationship between the two of them(improving health, neutral, degrading health).
Return a tau score that will reflect the power of the interaction between the 2 elements and also if it's negative or positive
return the result through a json object, The response must be in the following JSON format:
            {
                "food": "",
                "drug": "",
                "relationship": "",
                "tau": 0
            }
            Return only the JSON object. """} ,
        {
            "role": "user",
            "content": text
        }
    ],
        response_format= { "type": "json_object" }
)

    return json.loads(completion.choices[0].message.content)

In [25]:
# fdi_map = tau_score() # take summarized text

fdi_map["tau"] = fdi_map.summarize.map(tau_score)

/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_19659/2855111671.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fdi_map["tau"] = fdi_map.summarize.map(tau_score)


In [26]:
fdi_map#.texts_ID.duplicated()

fdi_map.shape

(5, 6)

In [27]:
fdi_map["tau"]

0    {'food': 'high-calorie meal', 'drug': 'abemaci...
1    {'food': 'grapefruit juice', 'drug': 'fentanyl...
2    {'food': 'grapefruit juice', 'drug': 'docetaxe...
3    {'food': 'Ethanol', 'drug': 'Painkillers', 're...
4    {'food': 'ethanol', 'drug': 'dextromethorphan'...
Name: tau, dtype: object

In [28]:
# fdi_map["tau_score"] = fdi_map["tau"].map(lambda x:x["tau"])

In [29]:
fdi_map.tau.iloc[3]

{'food': 'Ethanol',
 'drug': 'Painkillers',
 'relationship': 'Improving health',
 'tau': 0.7}

In [30]:
fdi_map[['food_', 'drug_', 'relationship', 'tau_score']] = fdi_map['tau'].apply(pd.Series)


/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_19659/3934944602.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fdi_map[['food_', 'drug_', 'relationship', 'tau_score']] = fdi_map['tau'].apply(pd.Series)
/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_19659/3934944602.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fdi_map[['food_', 'drug_', 'relationship', 'tau_score']] = fdi_map['tau'].apply(pd.Series)
/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_19659/393494460

In [31]:
# for index, row in fdi_map.iterrows():
#     print(f"Row {index}: Food={row['food']}, Drug={row['drug']}, Relationship={row['relationship']}, Tau={row['tau']}")


for index,row in fdi_map[["summarize","tau_score"]].iterrows():
    print(f"""TAU Score:{row["tau_score"]} Description :{row["summarize"]} """)

TAU Score:0.6 Description : A high-calorie meal may increase the concentration of the drug abemaciclib, according to research published in the British Journal of Oncology. 
TAU Score:-0.8 Description : The World Health Organization (WHO) warns that the consumption of grapefruit juice during treatment with the opioid fentanyl may increase the risk of an adverse reaction to the drug. 
TAU Score:-0.35 Description : AUC (AUC) for docetaxel, a drug used to treat leukaemia, has been reduced to 35% after a trial with grapefruit juice. 
TAU Score:0.7 Description : Ethanol can be used as a treatment for painkiller overdoses. 
TAU Score:0.7 Description :Dextromethorphan and ethanol can be used as a treatment for alcohol addiction. 


In [32]:
fdi_map.drop(columns='tau', inplace= True)

/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_19659/3168122293.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fdi_map.drop(columns='tau', inplace= True)


In [33]:
fdi_map.iloc[1, 5]

'grapefruit juice'

In [34]:
fdi_map

texts_ID        food               drug  \
0         0  grapefruit        abemaciclib   
1         2  grapefruit           fentanyl   
2         7  grapefruit         paclitaxel   
3        11     ethanol  opioid analgesics   
4        13     ethanol   dextromethorphan   

                                          clean_text  \
0  Moderate Food Interaction||GENERALLY AVOID:  G...   
1  GENERALLY AVOID:  Consumption of grapefruit ju...   
2  Moderate Food Interaction||MONITOR:  Coadminis...   
3  Moderate Drug Interaction||GENERALLY AVOID:  E...   
4  Moderate Drug Interaction||GENERALLY AVOID:  T...   

                                           summarize              food_  \
0   A high-calorie meal may increase the concentr...  high-calorie meal   
1   The World Health Organization (WHO) warns tha...   grapefruit juice   
2   AUC (AUC) for docetaxel, a drug used to treat...   grapefruit juice   
3   Ethanol can be used as a treatment for painki...            Ethanol   
4  Dextromethorphan and ethanol can be used as a ...            ethanol   

              drug_              relationship  tau_score  
0       abemaciclib  increasing concentration       0.60  
1          fentanyl          degrading health      -0.80  
2         docetaxel          degrading health      -0.35  
3       Painkillers          Improving health       0.70  
4  dextromethorphan          improving health       0.70

In [35]:
# content_ = fdi_map.choices[0].message.content

In [36]:
# start_index = content_.find('{')  # Add 1 to exclude the start_char
# end_index = content_.find("}")+1
# json.load(fdi_map.choices[0].message.content[start_index:end_index].replace("""\n""",""))

In [37]:
# json.loads(fdi_map.choices[0].message.content)

In [1]:
%load_ext autoreload
%autoreload 2


In [15]:
from medisure.ml_logic.FDI import get_tau_score

fdi = get_tau_score()

/Users/raynasser/code/raynasser/MediSure/medisure/ml_logic/FDI.py:94: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  


Start Summarization...


Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Your max_length is set to 62, but your input_length is only 23. Since this is a summarization task, where outputs shorter th

KeyboardInterrupt: 

In [10]:
fdi.isnull().sum()

texts_ID      0
food          0
drug          0
clean_text    0
dtype: int64

In [13]:
fdi[fdi["clean_text"]=="nan"]

Empty DataFrame
Columns: [texts_ID, food, drug, clean_text]
Index: []

In [145]:
fdi_summ = pd.read_csv(os.path.join(foodrug,'fdi_summarization_results-2.csv'))
# fdi_summ.dropna(subset=['summarize'], inplace=True)

fdi_summ
fdi_summ.isna().sum()


texts_ID       0
food           0
drug           0
clean_text     0
summarize     23
dtype: int64

In [170]:
fdi_summ[fdi_summ.texts_ID == 417]


texts_ID     food       drug  \
318       417  epoxide  equetrotm   

                                            clean_text summarize  
318  Therefore, the potential exists for interactio...       NaN

In [158]:
def summarize(text):
    # Initialize the summarization pipeline (only once to avoid reloading in a loop)
    pipe = pipeline('summarization', model='sshleifer/distilbart-xsum-12-6')

    # Skip texts that are too short (e.g., fewer than 5 words)
    if len(text.split()) < 5:
        return 'Text too short for summarization'

    # Split text into chunks if it's too long for the model (token limit for distilbart is ~1024 tokens)
    max_chunk_size = 1024 // 4  # Approx 256 words (as 1 token is roughly ~4 characters)
    text_chunks = [text[i:i+max_chunk_size] for i in range(0, len(text), max_chunk_size)]

    summarized_text = []

    try:
        # Summarize each chunk and combine the summaries
        for chunk in text_chunks:
            summary = pipe(chunk, max_length=100, min_length=30, do_sample=False)
            summarized_text.append(summary[0]['summary_text'])

        # Join summarized chunks together
        return ' '.join(summarized_text)
    except Exception as e:
        return f'Error: {str(e)}'

In [159]:
fdi_summ_na = fdi_summ[fdi_summ.summarize.isna()].reset_index()
fdi_summ_na.drop(columns=['summarize', 'index'], inplace=True)

fdi_summ_na
fdi_summ_na["summarize"] = fdi_summ_na.clean_text.map(summarize)

Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.
Your max_length is set to 100, but your input_length is only 64. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=32)
Your max_length is set to 100, but your input_length is only 79. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=39)
Your max_length is set to 100, but your input_length is only 81. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=40)
Your max_length is set to 100, but your input_length is only 82. Since this is a summarization task, where 

In [161]:
fdi_summ_na

texts_ID                        food                      drug  \
0        417                     epoxide                 equetrotm   
1        467                  saquinavir                alfentanyl   
2        612                 pramipexole            cephalosporins   
3        740                          h+                       mtf   
4        800                  oleuropein        dihydro oleuropein   
5       1159                   vitamin k                 vitamin k   
6       1441                       apple               alendronate   
7       1612                         lys                       arg   
8       1942                         npj                       hpj   
9       1954              bornyl acetate  thiamine dilaurylsulfate   
10      2034  6',7'-dihydroxybergamottin                 dasatinib   
11      2098                      cu(ii)                     cd(ii   
12      2269                     oatp2b1         estrone-3-sulfate   
13      2330                        zinc                 captopril   
14      2352                  hesperidin         estrone-3-sulfate   
15      2371                  flavonoids           flavonoids-rich   
16      2428                  grapefruit                amlodipine   
17      2570                      citrus                  banpeiyu   
18      2650                   quercetin              atorvastatin   
19      2682              cinnamaldehyde                ampicillin   
20      2750                        salt                        a2   
21      7242        n-methyl-d-aspartate                 ketorolac   
22      8144                beta-lactose              beta-lactose   

                                           clean_text  \
0   Therefore, the potential exists for interactio...   
1   Garlic Capsules Garlic capsules should not be ...   
2   Other drugs eliminated via renal secretion: Po...   
3   Third, Solutol HS 15, polysorbate 40, and poly...   
4   A systematized virtual search of 932 conformer...   
5   Alarming factors causing non-TINR detected in ...   
6   The potential adverse interactions included de...   
7   We found that, among basic amino acids, l-orni...   
8   The intake of either NPJ or HPJ led to a decre...   
9   The reduction in spore numbers by each of the ...   
10  Among the 14 ingredients screened, only tanger...   
11  Mixtures of Cd(II)/Cu(II) and Zn(II)/Ca(II) de...   
12  Eight major flavonoids (naringin, naringenin, ...   
13  Antihypertensive medicines are to known to cau...   
14  Eight major flavonoids (naringin, naringenin, ...   
15  The effect of flavonoids on GSTs strongly depe...   
16  AUC ratios of drugs with and without grapefrui...   
17  Other citrus fruits (orange, lemon) do not hav...   
18  K(i) values of all three flavonoids determined...   
19  With Escherichia coli N00 666, thymol and cinn...   
20  Striatal adenosine has been shown to have a si...   
21  There are several adjuvants have been added to...   
22  Secondary forms of lactose malabsorption may b...   

                                            summarize  
0    carbamazepine has been used as an anti-inflam...  
1    The drug Fortovase (FORTOVASE) is an anti-fre...  
2   Drugs that are co-administered by the renal sy...  
3    Three compounds, including Solutol HS 15, hav...  
4   Three compounds have been identified as the so...  
5   Non-TINR has been identified as a cause of non...  
6    The results of a study into whether grape and...  
7    In a study of the effects of the amino acids ...  
8    A study has shown that the daily intake of tw...  
9    A study has shown that a single surfactant ca...  
10   A study has shown that tangeretin and nobilet...  
11   A study of Cd(II/Zn/Mg/Cd has revealed a rang...  
12   A study has shown that juices containing flav...  
13  Antihypertensive medicines, such as captopril ...  
14   A study has shown that juices containing flav...  
15   flavonoids - also known as GSTs - can be used...  
16

In [131]:
fdi_summ_na.iloc[6][4]

'The potential adverse interactions included decreased drug bioavailability (apple juice-fexofenadine, atenolol, aliskiren; orange juice-aliskiren, atenolol, celiprolol, montelukast, fluoroquinolones, alendronate; pomelo juice-sildenafil; grape juice-cyclosporine), increased bioavailability (Seville orange juice-felodipine, pomelo juice-cyclosporine, orange-aluminum containing antacids).. The potential adverse interactions included decreased drug bioavailability (apple juice-fexofenadine, atenolol, aliskiren; orange juice-aliskiren, atenolol, celiprolol, montelukast, fluoroquinolones, alendronate; pomelo juice-sildenafil; grape juice-cyclosporine), increased bioavailability (Seville orange juice-felodipine, pomelo juice-cyclosporine, orange-aluminum containing antacids).. The potential adverse interactions included decreased drug bioavailability (apple juice-fexofenadine, atenolol, aliskiren; orange juice-aliskiren, atenolol, celiprolol, montelukast, fluoroquinolones, alendronate; pome

In [167]:
len(fdi_summ_na.iloc[6][3])

25022

In [165]:
fdi_summ.iloc[3][4]

' Ethanol can be used as a treatment for painkiller overdoses.'

In [20]:
ddi_a = pd.read_csv(os.path.join(ddi, 'A_alimentary_tract_metabolism_drugs.csv'))#, index_col='id')

ddi_a


DDInterID_A                Drug_A  DDInterID_B  \
0      DDInter1263            Naltrexone     DDInter1   
1         DDInter1              Abacavir  DDInter1348   
2        DDInter58    Aluminum hydroxide   DDInter582   
3       DDInter112            Aprepitant   DDInter582   
4       DDInter138           Attapulgite   DDInter582   
...            ...                   ...          ...   
56362  DDInter1022          Lansoprazole   DDInter888   
56363  DDInter1675           Simvastatin   DDInter888   
56364  DDInter1906  Ursodeoxycholic acid   DDInter888   
56365  DDInter1318              Nystatin  DDInter1097   
56366  DDInter1622          Rosuvastatin  DDInter1097   

                        Drug_B     Level  
0                     Abacavir  Moderate  
1                     Orlistat  Moderate  
2                 Dolutegravir     Major  
3                 Dolutegravir     Minor  
4                 Dolutegravir     Major  
...                        ...       ...  
56362  Hydrocortisone butyrate   Unknown  
56363  Hydrocortisone butyrate   Unknown  
56364  Hydrocortisone butyrate   Unknown  
56365    Loteprednol etabonate   Unknown  
56366    Loteprednol etabonate   Unknown  

[56367 rows x 5 columns]

In [21]:
ddi_b = pd.read_csv(os.path.join(ddi, 'B_blood_drugs.csv'))#, index_col='id')

# ddi_b

In [22]:
ddi_d = pd.read_csv(os.path.join(ddi, 'D_dermatologicals_drugs.csv'))#, index_col='id')

# ddi_d

In [23]:
ddi_h = pd.read_csv(os.path.join(ddi, 'H_hormonal_drugs.csv'))#, index_col='id')

# ddi_h

In [24]:
ddi_l = pd.read_csv(os.path.join(ddi, 'L_antineoplastic_immunomodulating_agents_drugs.csv'))#, index_col='id')

# ddi_l

In [25]:
ddi_p = pd.read_csv(os.path.join(ddi, 'P_antiparasitic_insecticides_repellents_drugs.csv'))#, index_col='id')

# ddi_p

In [26]:
ddi_r = pd.read_csv(os.path.join(ddi, 'P_antiparasitic_insecticides_repellents_drugs.csv'))#, index_col='id')

# ddi_r

In [27]:
ddi_v = pd.read_csv(os.path.join(ddi, 'P_antiparasitic_insecticides_repellents_drugs.csv'))#, index_col='id')

# ddi_v

In [28]:

all_ddi = pd.concat([ddi_a, ddi_b, ddi_d, ddi_h, ddi_l, ddi_p, ddi_r, ddi_v], ignore_index=True)
all_ddi


DDInterID_A              Drug_A  DDInterID_B        Drug_B     Level
0       DDInter1263          Naltrexone     DDInter1      Abacavir  Moderate
1          DDInter1            Abacavir  DDInter1348      Orlistat  Moderate
2         DDInter58  Aluminum hydroxide   DDInter582  Dolutegravir     Major
3        DDInter112          Aprepitant   DDInter582  Dolutegravir     Minor
4        DDInter138         Attapulgite   DDInter582  Dolutegravir     Major
...             ...                 ...          ...           ...       ...
190775  DDInter1202       Metronidazole   DDInter964     Iopromide   Unknown
190776   DDInter893  Hydroxychloroquine  DDInter1942     Vitamin D   Unknown
190777  DDInter1202       Metronidazole   DDInter801     Galactose   Unknown
190778   DDInter134          Atovaquone   DDInter801     Galactose   Unknown
190779   DDInter134          Atovaquone   DDInter766   Fluticasone   Unknown

[190780 rows x 5 columns]

In [15]:
eda_pipeline(all_ddi)

_________________________________


Columns:
Index(['DDInterID_A', 'Drug_A', 'DDInterID_B', 'Drug_B', 'Level'], dtype='object')


_________________________________


'Total Rows: 190,780'

_________________________________


Unique data types:
[dtype('O')]
_________________________________


Describe the DataFrame (including categorical data):
        DDInterID_A         Drug_A DDInterID_B         Drug_B     Level
count        190780         190780      190780         190780    190780
unique         1738           1738        1833           1833         4
top     DDInter1855  Triamcinolone  DDInter513  Dexamethasone  Moderate
freq           1513           1513        1849           1849    110781
_________________________________


Number of duplicate rows: 49,381
_________________________________


Missing values per column:


Missing Values
DDInterID_A               0
Drug_A                    0
DDInterID_B               0
Drug_B                    0
Level                     0

DDInterID_A              Drug_A  DDInterID_B        Drug_B     Level
0       DDInter1263          Naltrexone     DDInter1      Abacavir  Moderate
1          DDInter1            Abacavir  DDInter1348      Orlistat  Moderate
2         DDInter58  Aluminum hydroxide   DDInter582  Dolutegravir     Major
3        DDInter112          Aprepitant   DDInter582  Dolutegravir     Minor
4        DDInter138         Attapulgite   DDInter582  Dolutegravir     Major
...             ...                 ...          ...           ...       ...
190775  DDInter1202       Metronidazole   DDInter964     Iopromide   Unknown
190776   DDInter893  Hydroxychloroquine  DDInter1942     Vitamin D   Unknown
190777  DDInter1202       Metronidazole   DDInter801     Galactose   Unknown
190778   DDInter134          Atovaquone   DDInter801     Galactose   Unknown
190779   DDInter134          Atovaquone   DDInter766   Fluticasone   Unknown

[190780 rows x 5 columns]

In [39]:
duplicated_rows = all_ddi[all_ddi.duplicated(keep=False)]


In [40]:
duplicated_rows[(duplicated_rows['DDInterID_A'] == 'DDInter134') & (duplicated_rows['DDInterID_B'] == 'DDInter1197')]

DDInterID_A      Drug_A  DDInterID_B          Drug_B     Level
8865    DDInter134  Atovaquone  DDInter1197  Metoclopramide  Moderate
175167  DDInter134  Atovaquone  DDInter1197  Metoclopramide  Moderate
180659  DDInter134  Atovaquone  DDInter1197  Metoclopramide  Moderate
186151  DDInter134  Atovaquone  DDInter1197  Metoclopramide  Moderate

In [44]:
all_ddi.drop_duplicates(inplace=True)

In [46]:
np.sum(all_ddi.DDInterID_A == 'DDInter1')

all_ddi[all_ddi.DDInterID_A == 'DDInter1'].duplicated().sum()

# duplicated_rows[(duplicated_rows['DDInterID_A'] == 'DDInter1') & (duplicated_rows['DDInterID_B'] == 'DDInter246')]

0

In [48]:
all_ddi.shape

print(f'Total Rows: {all_ddi.shape[0]:,}')

Total Rows: 141,399


In [55]:
all_ddi = all_ddi.applymap(lower)
all_ddi


DDInterID_A              Drug_A  DDInterID_B                 Drug_B  \
0       ddinter1263          naltrexone     ddinter1               abacavir   
1          ddinter1            abacavir  ddinter1348               orlistat   
2         ddinter58  aluminum hydroxide   ddinter582           dolutegravir   
3        ddinter112          aprepitant   ddinter582           dolutegravir   
4        ddinter138         attapulgite   ddinter582           dolutegravir   
...             ...                 ...          ...                    ...   
179784   ddinter893  hydroxychloroquine   ddinter511         desvenlafaxine   
179787   ddinter893  hydroxychloroquine  ddinter1097  loteprednol etabonate   
179790   ddinter893  hydroxychloroquine    ddinter19         acetylcysteine   
179792   ddinter893  hydroxychloroquine  ddinter1942              vitamin d   
179794   ddinter134          atovaquone   ddinter801              galactose   

           Level  
0       moderate  
1       moderate  
2          major  
3          minor  
4          major  
...          ...  
179784   unknown  
179787   unknown  
179790   unknown  
179792   unknown  
179794   unknown  

[141399 rows x 5 columns]

In [56]:
all_ddi.duplicated().sum()

0

In [57]:
all_ddi.columns

Index(['DDInterID_A', 'Drug_A', 'DDInterID_B', 'Drug_B', 'Level'], dtype='object')

In [106]:


def ddi_tau_score(drug_a, drug_b, level):
    # Define the API key and endpoint
    API_KEY = os.environ.get("API_KEY")

    # Set up headers for the API request
    client = openai.OpenAI(api_key=API_KEY)

    # Prepare the API call to analyze drug-drug interaction based on level
    prompt = f"""
    You are tasked with determining the interaction mechanism between two drugs.
    The drugs are:
    - Drug A: {drug_a}
    - Drug B: {drug_b}

    The level of interaction is: {level}

    Based on this information, describe the interaction mechanism (inhibition, synergy, antagonism, etc.), and return a tau score that reflects the strength of the interaction. Return the result as a JSON object in the following format:
        {{
            "drug_a": "{drug_a}",
            "drug_b": "{drug_b}",
            "mechanism": "",
            "tau": 0
        }}
    Only return the JSON object.
    """

    try:
        # API call to OpenAI
        completion = client.chat.completions.create(
            model="gpt-4o",
            messages=[
                {"role": "user", "content": prompt}
            ]
        )

        # Log the raw response for debugging
        response_content = completion.choices[0].message.content
        print(f"Response for {drug_a} and {drug_b}: {response_content}")

        # Clean up the response to remove any extra formatting markers like ```json or ```
        response_content = response_content.strip('```json').strip('```').strip()

        # Check if response is empty or invalid
        if not response_content.strip():
            print(f"Empty response for {drug_a} and {drug_b}")
            return {
                "drug_a": drug_a,
                "drug_b": drug_b,
                "mechanism": "unknown",
                "tau": 0
            }

        # Try to load the JSON response
        return json.loads(response_content)

    except (json.JSONDecodeError, KeyError) as e:
        # Handle JSON decode errors or missing keys
        print(f"Error processing response for {drug_a} and {drug_b}: {e}")
        return {
            "drug_a": drug_a,
            "drug_b": drug_b,
            "mechanism": "unknown",
            "tau": 0
        }

    except Exception as e:
        # Catch all other errors (e.g., connection issues)
        print(f"An error occurred: {e}")
        return {
            "drug_a": drug_a,
            "drug_b": drug_b,
            "mechanism": "unknown",
            "tau": 0
        }


In [86]:
# import os
# import json
# import openai

# def ddi_tau_score(drug_a, drug_b, level):
#     # Define the API key and endpoint
#     API_KEY = os.environ.get("API_KEY")

#     # Set up headers for the API request
#     client = openai.OpenAI(api_key=API_KEY)

#     # Create the request with structured roles (assistant and user), formatting the drug names
#     try:
#         completion = client.chat.completions.create(
#             model="gpt-4o",
#             messages=[
#                 {"role": "assistant", "content": f"""You are tasked with determining the interaction mechanism between two drugs.
#                 The drugs are:
#                 - Drug A: {drug_a}
#                 - Drug B: {drug_b}

#                 The level of interaction is: {level}

#                 Based on this information, describe the interaction mechanism (inhibition, synergy, antagonism, etc.), and return a tau score that reflects the strength of the interaction.
#                 Return the result through a JSON object. The response must be in the following JSON format:
#                 {{
#                     "drug_a": "{drug_a}",
#                     "drug_b": "{drug_b}",
#                     "mechanism": "",
#                     "tau": 0
#                 }}
#                 Return only the JSON object."""},
#                 {"role": "user", "content": f"The interaction level is: {level}"}
#             ],
#             response_format={"type": "json_object"}
#         )

#         # Log the raw response for debugging
#         response_content = completion.choices[0].message.content
#         print(f"Response for {drug_a} and {drug_b}: {response_content}")

#         # Validate that the response is a valid JSON string
#         if response_content.strip().startswith("{") and response_content.strip().endswith("}"):
#             # Try to load the JSON response
#             return json.loads(response_content)
#         else:
#             print(f"Invalid JSON format for {drug_a} and {drug_b}")
#             return {
#                 "drug_a": drug_a,
#                 "drug_b": drug_b,
#                 "mechanism": "unknown",
#                 "tau": 0
#             }

#     except (json.JSONDecodeError, KeyError) as e:
#         # Handle JSON decode errors or missing keys
#         print(f"Error processing response for {drug_a} and {drug_b}: {e}")
#         return {
#             "drug_a": drug_a,
#             "drug_b": drug_b,
#             "mechanism": "unknown",
#             "tau": 0
#         }

#     except Exception as e:
#         # Catch all other errors (e.g., connection issues)
#         print(f"An error occurred: {e}")
#         return {
#             "drug_a": drug_a,
#             "drug_b": drug_b,
#             "mechanism": "unknown",
#             "tau": 0
#         }


In [90]:
all_ddi50 = all_ddi.head(7)
all_ddi50

DDInterID_A              Drug_A  DDInterID_B        Drug_B     Level
0  ddinter1263          naltrexone     ddinter1      abacavir  moderate
1     ddinter1            abacavir  ddinter1348      orlistat  moderate
2    ddinter58  aluminum hydroxide   ddinter582  dolutegravir     major
3   ddinter112          aprepitant   ddinter582  dolutegravir     minor
4   ddinter138         attapulgite   ddinter582  dolutegravir     major
5   ddinter270     calcium acetate   ddinter582  dolutegravir     major
6   ddinter271   calcium carbonate   ddinter582  dolutegravir     major

In [89]:
# Select a specific row by index (for example, the first row)
single_row = all_ddi.iloc[3]

# Extract the values for Drug_A, Drug_B, and Level from the row
drug_a = single_row['Drug_A']
drug_b = single_row['Drug_B']
level = single_row['Level']

# Call the tau_score function for just this one row
result = ddi_tau_score(drug_a, drug_b, level)

# Print the result
print(result)


Response for aprepitant and dolutegravir: ```json
{
    "drug_a": "aprepitant",
    "drug_b": "dolutegravir",
    "mechanism": "inhibition",
    "tau": 0.2
}
```
Error processing response for aprepitant and dolutegravir: Expecting value: line 1 column 1 (char 0)
{'drug_a': 'aprepitant', 'drug_b': 'dolutegravir', 'mechanism': 'unknown', 'tau': 0}


In [71]:
all_ddi.Level.value_counts()

moderate    84015
unknown     26716
major       24190
minor        6478
Name: Level, dtype: int64

In [107]:
# all_ddi50['Interaction_Details'] = all_ddi.apply(
#         lambda row: ddi_tau_score(row['Drug_A'], row['Drug_B'], row['Level']),
#         axis=1
#     )


all_ddi50['Interaction_Details'] = all_ddi50.apply(
    lambda row: ddi_tau_score(row['Drug_A'],
                              row['Drug_B'],
                              row['Level']),
    axis=1)



all_ddi50[['drug_a_', 'drug_b_', 'mechanism', 'tau']] = all_ddi50['Interaction_Details'].apply(pd.Series)
#     lambda row: pd.Series(ddi_tau_score(row['Drug_A'],
#                                         row['Drug_B'],
#                                         row['Level'])),
#     axis=1
# )


Response for naltrexone and abacavir: ```json
{
    "drug_a": "naltrexone",
    "drug_b": "abacavir",
    "mechanism": "antagonism",
    "tau": 0.4
}
```
Response for abacavir and orlistat: ```json
{
    "drug_a": "abacavir",
    "drug_b": "orlistat",
    "mechanism": "antagonism",
    "tau": 0.3
}
```
Response for aluminum hydroxide and dolutegravir: ```json
{
    "drug_a": "aluminum hydroxide",
    "drug_b": "dolutegravir",
    "mechanism": "antagonism",
    "tau": -0.6
}
```
Response for aprepitant and dolutegravir: ```json
{
    "drug_a": "aprepitant",
    "drug_b": "dolutegravir",
    "mechanism": "inhibition",
    "tau": 0.1
}
```
Response for attapulgite and dolutegravir: ```json
{
    "drug_a": "attapulgite",
    "drug_b": "dolutegravir",
    "mechanism": "inhibition",
    "tau": 0.8
}
```
Response for calcium acetate and dolutegravir: ```json
{
    "drug_a": "calcium acetate",
    "drug_b": "dolutegravir",
    "mechanism": "antagonism",
    "tau": 0.8
}
```
Response for calciu

/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_97665/2686449487.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  all_ddi50['Interaction_Details'] = all_ddi50.apply(
/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_97665/2686449487.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  all_ddi50[['drug_a_', 'drug_b_', 'mechanism', 'tau']] = all_ddi50['Interaction_Details'].apply(pd.Series)


In [109]:
# all_ddi50.to_csv('/Users/raynasser/Downloads/DSproj/x/r.csv')

all_ddi50

DDInterID_A              Drug_A  DDInterID_B        Drug_B     Level  \
0  ddinter1263          naltrexone     ddinter1      abacavir  moderate   
1     ddinter1            abacavir  ddinter1348      orlistat  moderate   
2    ddinter58  aluminum hydroxide   ddinter582  dolutegravir     major   
3   ddinter112          aprepitant   ddinter582  dolutegravir     minor   
4   ddinter138         attapulgite   ddinter582  dolutegravir     major   
5   ddinter270     calcium acetate   ddinter582  dolutegravir     major   
6   ddinter271   calcium carbonate   ddinter582  dolutegravir     major   

                                 Interaction_Details             drug_a_  \
0  {'drug_a': 'naltrexone', 'drug_b': 'abacavir',...          naltrexone   
1  {'drug_a': 'abacavir', 'drug_b': 'orlistat', '...            abacavir   
2  {'drug_a': 'aluminum hydroxide', 'drug_b': 'do...  aluminum hydroxide   
3  {'drug_a': 'aprepitant', 'drug_b': 'dolutegrav...          aprepitant   
4  {'drug_a': 'attapulgite', 'drug_b': 'dolutegra...         attapulgite   
5  {'drug_a': 'calcium acetate', 'drug_b': 'dolut...     calcium acetate   
6  {'drug_a': 'calcium carbonate', 'drug_b': 'dol...   calcium carbonate   

        drug_b_   mechanism  tau  
0      abacavir  antagonism  0.4  
1      orlistat  antagonism  0.3  
2  dolutegravir  antagonism -0.6  
3  dolutegravir  inhibition  0.1  
4  dolutegravir  inhibition  0.8  
5  dolutegravir  antagonism  0.8  
6  dolutegravir  antagonism  0.8

In [120]:
ddi_all = ddi_data()

ddi_all

Start getting ddi...
Response for naltrexone and abacavir: ```json
{
    "drug_a": "naltrexone",
    "drug_b": "abacavir",
    "mechanism": "antagonism",
    "tau": 0.3
}
```
Response for abacavir and orlistat: ```json
{
    "drug_a": "abacavir",
    "drug_b": "orlistat",
    "mechanism": "antagonism",
    "tau": 0.4
}
```
Response for aluminum hydroxide and dolutegravir: ```json
{
    "drug_a": "aluminum hydroxide",
    "drug_b": "dolutegravir",
    "mechanism": "antagonism",
    "tau": -0.7
}
```
Response for aprepitant and dolutegravir: ```json
{
    "drug_a": "aprepitant",
    "drug_b": "dolutegravir",
    "mechanism": "inhibition",
    "tau": 0.1
}
```
Response for attapulgite and dolutegravir: ```json
{
    "drug_a": "attapulgite",
    "drug_b": "dolutegravir",
    "mechanism": "",
    "tau": 0
}
```
Response for calcium acetate and dolutegravir: ```json
{
    "drug_a": "calcium acetate",
    "drug_b": "dolutegravir",
    "mechanism": "absorption inhibition",
    "tau": 0.8
}
```

KeyboardInterrupt: 

In [118]:
# all_ddi['Tau_Score'] = all_ddi['Interaction_Details'].apply(lambda x: x['tau'])


In [77]:
# import os
# import json
# import openai
# import time

# def drug_interaction_effects(drug_a, drug_b, retries=3):
#     # Define the API key and endpoint
#     API_KEY = os.environ.get("API_KEY")

#     # Set up headers for the API request
#     client = openai.OpenAI(api_key=API_KEY)

#     prompt = f"""
#     You are tasked with analyzing the effects of two drugs when taken together. The drugs are:
#     - Drug A: {drug_a}
#     - Drug B: {drug_b}

#     Describe the potential effects when these two drugs are co-administered, including any side effects, possible increased toxicity, synergistic effects, or contraindications. Return the result as a JSON object in the following format:
#         {{
#             "drug_a": "{drug_a}",
#             "drug_b": "{drug_b}",
#             "effects": [
#                 {{
#                     "effect": "",
#                     "severity": "",
#                     "details": ""
#                 }}
#             ]
#         }}
#     Only return the JSON object.
#     """

#     for attempt in range(retries):
#         try:
#             # API call to OpenAI
#             completion = client.chat.completions.create(
#                 model="gpt-4o",
#                 messages=[
#                     {"role": "user", "content": prompt}
#                 ]
#             )

#             # Log the raw response for debugging
#             response_content = completion.choices[0].message.content
#             print(f"Raw response for {drug_a} and {drug_b}: {response_content}")

#             # Check if response is empty or invalid
#             if not response_content.strip():
#                 print(f"Empty response for {drug_a} and {drug_b}, retrying...")
#                 continue  # Retry the request

#             # Try to load the JSON response
#             return json.loads(response_content)

#         except (json.JSONDecodeError, KeyError) as e:
#             print(f"Error processing response for {drug_a} and {drug_b}: {e}")
#             continue  # Retry the request

#         except Exception as e:
#             print(f"An error occurred: {e}")
#             time.sleep(1)  # Add a delay before retrying

#     # After retrying, if all attempts fail, return a default response
#     return {
#         "drug_a": drug_a,
#         "drug_b": drug_b,
#         "effects": [
#             {
#                 "effect": "unknown",
#                 "severity": "unknown",
#                 "details": "Unable to retrieve interaction details after retries."
#             }
#         ]
#     }


In [79]:
# # Example interaction between naltrexone and abacavir
# result = drug_interaction_effects("naltrexone", "abacavir")

# # Output the result
# print(json.dumps(result, indent=4))


In [7]:
medi = pd.read_csv('/Users/raynasser/code/raynasser/MediSure/data/raw_data/medicine_dataset.csv')#, index_col='id')
medi

/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_26611/1028064522.py:1: DtypeWarning: Columns (42,43,44,45,46,47,48) have mixed types. Specify dtype option on import or set low_memory=False.
  medi = pd.read_csv('/Users/raynasser/code/raynasser/MediSure/data/raw_data/medicine_dataset.csv')#, index_col='id')


id                                  name  \
0            1              augmentin 625 duo tablet   
1            2                   azithral 500 tablet   
2            3                      ascoril ls syrup   
3            4                  allegra 120mg tablet   
4            5                        avil 25 tablet   
...        ...                                   ...   
248213  248214  zestrain 100mg/325mg/250mg tablet mr   
248214  248215              zoxinace 200mg tablet sr   
248215  248216                     zivex 25mg tablet   
248216  248217               zi fast 500mg injection   
248217  248218             zyvocol 1% dusting powder   

                                substitute0             substitute1  \
0            Penciclav 500 mg/125 mg Tablet  Moxikind-CV 625 Tablet   
1                   Zithrocare 500mg Tablet         Azax 500 Tablet   
2                           Solvin LS Syrup       Ambrodil-LX Syrup   
3                              Lcfex Tablet     Etofex 120mg Tablet   
4                        Eralet 25mg Tablet                     NaN   
...                                     ...                     ...   
248213  Aclotec MR 100mg/325mg/250mg Tablet       SAMONEC MR TABLET   
248214                Algic 200mg Tablet SR  Topnac 200mg Tablet SR   
248215                  HD Zine 25mg Tablet    Hydrocas 25mg Tablet   
248216                Zycin 500mg Injection  Aziwok 500mg Injection   
248217              Canazole Dusting Powder  Clotrex Dusting Powder   

                                substitute2  \
0                   Moxiforce-CV 625 Tablet   
1                           Zady 500 Tablet   
2                         Zerotuss XP Syrup   
3                      Nexofex 120mg Tablet   
4                                       NaN   
...                                     ...   
248213  Uniclof 100mg/325mg/250mg Tablet MR   
248214               Kindac 200mg Tablet SR   
248215                      Hyzox 25 Tablet   
248216               Azirow 500mg Injection   
248217                 AF -C Dusting Powder   

                               substitute3  \
0                       Fightox 625 Tablet   
1                    Cazithro 500mg Tablet   
2                           Capex LS Syrup   
3                      Fexise 120mg Tablet   
4                                      NaN   
...                                    ...   
248213  Macito 100mg/325mg/250mg Tablet MR   
248214            Ultranac 200mg Tablet SR   
248215                   Hydil 25mg Tablet   
248216             Toracin 500mg Injection   
248217              Klo-Aid Dusting Powder   

                                substitute4  \
0                   Novamox CV 625mg Tablet   
1                     Trulimax 500mg Tablet   
2                           Broxum LS Syrup   
3                      Histafree 120 Tablet   
4                                       NaN   
...                                     ...   
248213  Rumatin 100mg/325mg/250mg Tablet MR   
248214               Bignac 200mg Tablet SR   
248215                   Zyzine 25mg Tablet   
248216               Azymed 500mg Injection   
248217               Nuforce Dusting Powder   

                                              sideEffect0       sideEffect1  \
0                                                Vomiting            Nausea   
1                                                Vomiting            Nausea   
2                                                  Nausea          Vomiting   
3                                                Headache        Drowsiness   
4                                              Sleepiness  Dryness in mouth   
...                                                   ...               ...   
248213                                             Nausea          Vomiting   
248214                                          Dizziness       Indigestion   
248215                                           Sedation            Nausea   
248216  Injec

In [8]:
def lower(text):
    try:
        return text.lower()
    except:
        return text




medi.applymap(lower)

id                                  name  \
0            1              augmentin 625 duo tablet   
1            2                   azithral 500 tablet   
2            3                      ascoril ls syrup   
3            4                  allegra 120mg tablet   
4            5                        avil 25 tablet   
...        ...                                   ...   
248213  248214  zestrain 100mg/325mg/250mg tablet mr   
248214  248215              zoxinace 200mg tablet sr   
248215  248216                     zivex 25mg tablet   
248216  248217               zi fast 500mg injection   
248217  248218             zyvocol 1% dusting powder   

                                substitute0             substitute1  \
0            penciclav 500 mg/125 mg tablet  moxikind-cv 625 tablet   
1                   zithrocare 500mg tablet         azax 500 tablet   
2                           solvin ls syrup       ambrodil-lx syrup   
3                              lcfex tablet     etofex 120mg tablet   
4                        eralet 25mg tablet                     NaN   
...                                     ...                     ...   
248213  aclotec mr 100mg/325mg/250mg tablet       samonec mr tablet   
248214                algic 200mg tablet sr  topnac 200mg tablet sr   
248215                  hd zine 25mg tablet    hydrocas 25mg tablet   
248216                zycin 500mg injection  aziwok 500mg injection   
248217              canazole dusting powder  clotrex dusting powder   

                                substitute2  \
0                   moxiforce-cv 625 tablet   
1                           zady 500 tablet   
2                         zerotuss xp syrup   
3                      nexofex 120mg tablet   
4                                       NaN   
...                                     ...   
248213  uniclof 100mg/325mg/250mg tablet mr   
248214               kindac 200mg tablet sr   
248215                      hyzox 25 tablet   
248216               azirow 500mg injection   
248217                 af -c dusting powder   

                               substitute3  \
0                       fightox 625 tablet   
1                    cazithro 500mg tablet   
2                           capex ls syrup   
3                      fexise 120mg tablet   
4                                      NaN   
...                                    ...   
248213  macito 100mg/325mg/250mg tablet mr   
248214            ultranac 200mg tablet sr   
248215                   hydil 25mg tablet   
248216             toracin 500mg injection   
248217              klo-aid dusting powder   

                                substitute4  \
0                   novamox cv 625mg tablet   
1                     trulimax 500mg tablet   
2                           broxum ls syrup   
3                      histafree 120 tablet   
4                                       NaN   
...                                     ...   
248213  rumatin 100mg/325mg/250mg tablet mr   
248214               bignac 200mg tablet sr   
248215                   zyzine 25mg tablet   
248216               azymed 500mg injection   
248217               nuforce dusting powder   

                                              sideEffect0       sideEffect1  \
0                                                vomiting            nausea   
1                                                vomiting            nausea   
2                                                  nausea          vomiting   
3                                                headache        drowsiness   
4                                              sleepiness  dryness in mouth   
...                                                   ...               ...   
248213                                             nausea          vomiting   
248214                                          dizziness       indigestion   
248215                                           sedation            nausea   
248216  injec

In [9]:
medi = medi.drop_duplicates(subset='name', keep='last').reset_index(drop=True)
medi.shape

(222825, 58)

In [28]:
import re


# pattern = r'^([\w\s\-\/\u00C0-\u02AF]+)\s*([\dmg\/]+(?:mg|g|ml)?)?\s*(.*)$'

def extract_medication_info(med_str):
    # Regular expression to capture the name, dosage (with slashes), and form
    # pattern = r'^([a-zA-Z\s]+)\s([\dmg/]+)\s*(.*)$'
    # pattern = r'^([a-zA-Z\s\-]+)\s*(\d*mg)?\s*(.*)$'
    # pattern = r'^([\w\s\-\u00C0-\u02AF]+)\s*(\d*mg|\d+)?\s*(.*)$'

    patterns = [
        r'^([a-zA-Z\s]+)\s([\dmg/]+)\s*(.*)$',
        r'^([a-zA-Z\s\-]+)\s*(\d*mg)?\s*(.*)$',
        r'^([\w\s\-\u00C0-\u02AF]+)\s*(\d*mg|\d+)?\s*(.*)$'
    ]

    for pattern in patterns:
        match = re.match(pattern, med_str)
        if match:
            # Safely extract the groups and strip spaces
            name = match.group(1).strip() if match.group(1) else ""
            dosage = match.group(2).strip() if match.group(2) else ""
            form = match.group(3).strip() if match.group(3) else ""
            return pd.Series([name, dosage, form])

    # If no match found, return None for each column
    return pd.Series([None, None, None])





# medi.name.map(extract_medication_info)

medi[['name_', 'dosage', 'form']] = medi['name'].apply(extract_medication_info)
medi

id                                  name  \
0            1              augmentin 625 duo tablet   
1            2                   azithral 500 tablet   
2            3                      ascoril ls syrup   
3            5                        avil 25 tablet   
4            6                      allegra-m tablet   
...        ...                                   ...   
222820  248214  zestrain 100mg/325mg/250mg tablet mr   
222821  248215              zoxinace 200mg tablet sr   
222822  248216                     zivex 25mg tablet   
222823  248217               zi fast 500mg injection   
222824  248218             zyvocol 1% dusting powder   

                                substitute0             substitute1  \
0            Penciclav 500 mg/125 mg Tablet  Moxikind-CV 625 Tablet   
1                   Zithrocare 500mg Tablet         Azax 500 Tablet   
2                           Solvin LS Syrup       Ambrodil-LX Syrup   
3                        Eralet 25mg Tablet                     NaN   
4                        Emlukast-FX Tablet       LCFEX-Mont Tablet   
...                                     ...                     ...   
222820  Aclotec MR 100mg/325mg/250mg Tablet       SAMONEC MR TABLET   
222821                Algic 200mg Tablet SR  Topnac 200mg Tablet SR   
222822                  HD Zine 25mg Tablet    Hydrocas 25mg Tablet   
222823                Zycin 500mg Injection  Aziwok 500mg Injection   
222824              Canazole Dusting Powder  Clotrex Dusting Powder   

                                substitute2  \
0                   Moxiforce-CV 625 Tablet   
1                           Zady 500 Tablet   
2                         Zerotuss XP Syrup   
3                                       NaN   
4                   Fixar 10mg/120mg Tablet   
...                                     ...   
222820  Uniclof 100mg/325mg/250mg Tablet MR   
222821               Kindac 200mg Tablet SR   
222822                      Hyzox 25 Tablet   
222823               Azirow 500mg Injection   
222824                 AF -C Dusting Powder   

                               substitute3  \
0                       Fightox 625 Tablet   
1                    Cazithro 500mg Tablet   
2                           Capex LS Syrup   
3                                      NaN   
4                       Histakind-M Tablet   
...                                    ...   
222820  Macito 100mg/325mg/250mg Tablet MR   
222821            Ultranac 200mg Tablet SR   
222822                   Hydil 25mg Tablet   
222823             Toracin 500mg Injection   
222824              Klo-Aid Dusting Powder   

                                substitute4  \
0                   Novamox CV 625mg Tablet   
1                     Trulimax 500mg Tablet   
2                           Broxum LS Syrup   
3                                       NaN   
4                        Histafree-M Tablet   
...                                     ...   
222820  Rumatin 100mg/325mg/250mg Tablet MR   
222821               Bignac 200mg Tablet SR   
222822                   Zyzine 25mg Tablet   
222823               Azymed 500mg Injection   
222824               Nuforce Dusting Powder   

                                              sideEffect0       sideEffect1  \
0                                                Vomiting            Nausea   
1                                                Vomiting            Nausea   
2                                                  Nausea          Vomiting   
3                                              Sleepiness  Dryness in mouth   
4                                                  Nausea          Diarrhea   
...                                                   ...               ...   
222820                                             Nausea          Vomiting   
222821                                          Dizziness       Indigestion   
222822                                           Sedation            Nausea   
222823  Injec

In [29]:
medi.name_.isna().sum()

0

In [30]:
medi.columns.to_series

<bound method Index.to_series of Index(['id', 'name', 'substitute0', 'substitute1', 'substitute2',
       'substitute3', 'substitute4', 'sideEffect0', 'sideEffect1',
       'sideEffect2', 'sideEffect3', 'sideEffect4', 'sideEffect5',
       'sideEffect6', 'sideEffect7', 'sideEffect8', 'sideEffect9',
       'sideEffect10', 'sideEffect11', 'sideEffect12', 'sideEffect13',
       'sideEffect14', 'sideEffect15', 'sideEffect16', 'sideEffect17',
       'sideEffect18', 'sideEffect19', 'sideEffect20', 'sideEffect21',
       'sideEffect22', 'sideEffect23', 'sideEffect24', 'sideEffect25',
       'sideEffect26', 'sideEffect27', 'sideEffect28', 'sideEffect29',
       'sideEffect30', 'sideEffect31', 'sideEffect32', 'sideEffect33',
       'sideEffect34', 'sideEffect35', 'sideEffect36', 'sideEffect37',
       'sideEffect38', 'sideEffect39', 'sideEffect40', 'sideEffect41', 'use0',
       'use1', 'use2', 'use3', 'use4', 'Chemical Class', 'Habit Forming',
       'Therapeutic Class', 'Action Class', 'name_

In [39]:
medi.isna().sum()

id                       0
name                     0
substitute0              0
substitute1              0
substitute2              0
                     ...  
Therapeutic Class        0
Action Class         99286
name_                    0
dosage                   0
form                     0
Length: 61, dtype: int64

In [32]:
# medi.fillna({
#     'substitute0': 'No substitute',
#     'substitute1': 'No substitute',
#     'substitute2': 'No substitute',
#     'substitute3': 'No substitute',
#     'substitute4': 'No substitute',
#     'sideEffect2': 'Not specified'
# }, inplace=True)

In [33]:
substitute_cols = [col for col in medi.columns if col.startswith('substitute')]
medi[substitute_cols] = medi[substitute_cols].fillna('No substitute')


side_effect_cols = [col for col in medi.columns if col.startswith('sideEffect')]
medi[side_effect_cols] = medi[side_effect_cols].fillna('No other side effect')


use_cols = [col for col in medi.columns if col.startswith('use')]
medi[use_cols] = medi[use_cols].fillna('Not specified')

In [35]:
medi['Therapeutic Class'].fillna('Other', inplace=True)

In [38]:
medi['Chemical Class'].isna().sum()

medi['Chemical Class'].fillna('Other', inplace=True)

In [41]:
medi.to_csv('/Users/raynasser/code/raynasser/MediSure/data/raw_data/final_medi.csv')

In [43]:
fin_medi = pd.read_csv('/Users/raynasser/code/raynasser/MediSure/data/raw_data/final_medi.csv')
fin_medi

Unnamed: 0      id                                  name  \
0                0       1              augmentin 625 duo tablet   
1                1       2                   azithral 500 tablet   
2                2       3                      ascoril ls syrup   
3                3       5                        avil 25 tablet   
4                4       6                      allegra-m tablet   
...            ...     ...                                   ...   
222820      222820  248214  zestrain 100mg/325mg/250mg tablet mr   
222821      222821  248215              zoxinace 200mg tablet sr   
222822      222822  248216                     zivex 25mg tablet   
222823      222823  248217               zi fast 500mg injection   
222824      222824  248218             zyvocol 1% dusting powder   

                                substitute0             substitute1  \
0            Penciclav 500 mg/125 mg Tablet  Moxikind-CV 625 Tablet   
1                   Zithrocare 500mg Tablet         Azax 500 Tablet   
2                           Solvin LS Syrup       Ambrodil-LX Syrup   
3                        Eralet 25mg Tablet           No substitute   
4                        Emlukast-FX Tablet       LCFEX-Mont Tablet   
...                                     ...                     ...   
222820  Aclotec MR 100mg/325mg/250mg Tablet       SAMONEC MR TABLET   
222821                Algic 200mg Tablet SR  Topnac 200mg Tablet SR   
222822                  HD Zine 25mg Tablet    Hydrocas 25mg Tablet   
222823                Zycin 500mg Injection  Aziwok 500mg Injection   
222824              Canazole Dusting Powder  Clotrex Dusting Powder   

                                substitute2  \
0                   Moxiforce-CV 625 Tablet   
1                           Zady 500 Tablet   
2                         Zerotuss XP Syrup   
3                             No substitute   
4                   Fixar 10mg/120mg Tablet   
...                                     ...   
222820  Uniclof 100mg/325mg/250mg Tablet MR   
222821               Kindac 200mg Tablet SR   
222822                      Hyzox 25 Tablet   
222823               Azirow 500mg Injection   
222824                 AF -C Dusting Powder   

                               substitute3  \
0                       Fightox 625 Tablet   
1                    Cazithro 500mg Tablet   
2                           Capex LS Syrup   
3                            No substitute   
4                       Histakind-M Tablet   
...                                    ...   
222820  Macito 100mg/325mg/250mg Tablet MR   
222821            Ultranac 200mg Tablet SR   
222822                   Hydil 25mg Tablet   
222823             Toracin 500mg Injection   
222824              Klo-Aid Dusting Powder   

                                substitute4  \
0                   Novamox CV 625mg Tablet   
1                     Trulimax 500mg Tablet   
2                           Broxum LS Syrup   
3                             No substitute   
4                        Histafree-M Tablet   
...                                     ...   
222820  Rumatin 100mg/325mg/250mg Tablet MR   
222821               Bignac 200mg Tablet SR   
222822                   Zyzine 25mg Tablet   
222823               Azymed 500mg Injection   
222824               Nuforce Dusting Powder   

                                              sideEffect0       sideEffect1  \
0                                                Vomiting            Nausea   
1                                                Vomiting            Nausea   
2                                                  Nausea          Vomiting   
3                                              Sleepiness  Dryness in mouth   
4                                                  Nausea          Diarrhea   
...                                                   ...               ...   
222820                                             Nausea          Vomiting   
222821                 

In [1]:
from medisure.ml_logic.InChi import uniq_drugs_key

fdi_key = uniq_drugs_key()
fdi_key

/Users/raynasser/.pyenv/versions/3.10.6/envs/MediSure/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Error: Unable to fetch data for ace inhibitors. Status code: 404
Error: Unable to fetch data for citrates. Status code: 404
Error: Unable to fetch data for h2-receptor antagonists. Status code: 404
Error: Unable to fetch data for benzodiazepines. Status code: 404
Error: Unable to fetch data for adrenergic bronchodilators. Status code: 404
Error: Unable to fetch data for hmg-coa reductase inhibitors. Status code: 404
Error: Unable to fetch data for calcium channel blockers. Status code: 404
Error: Unable to fetch data for 5-fluorouracil (. Status code: 404
Error: Unable to fetch data for rechallenge. Status code: 404
Error: Unable to fetch data for tricyclic antidepressant. Status code: 404
Error: Unable to fetch data for angiotensin ii receptor blockers. Status code: 404
Error: Unable to fetch data for phenothiazines. Status code: 404
Error: Unable to fetch data for proton pump inhibitors. Status code: 404
Error: Unable to fetch data for quinolone antibiotics. Status code: 404
Error: U

Unnamed: 0                     drug  \
0              0              abemaciclib   
1              1                 fentanyl   
2              2               paclitaxel   
3              3        opioid analgesics   
4              4         dextromethorphan   
...          ...                      ...   
4461        4461          hyaluronic acid   
4462        4462                   kazdin   
4463        4463                    mhspc   
4464        4464  anti-inflammatory drugs   
4465        4465                 tibolone   

                                                 SMILES  \
0     CCN1CCN(CC1)CC2=CN=C(C=C2)NC3=NC=C(C(=N3)C4=CC...   
1          CCC(=O)N(C1CCN(CC1)CCC2=CC=CC=C2)C3=CC=CC=C3   
2     CC1=C2[C@H](C(=O)[C@@]3([C@H](C[C@@H]4[C@]([C@...   
3     CCC(=O)N(C1CCN(CC1)CCC2=CC=CC=C2)C3=CC=CC=C3.C...   
4       CN1CC[C@@]23CCCC[C@@H]2[C@@H]1CC4=C3C=C(C=C4)OC   
...                                                 ...   
4461                                          Not Found   
4462                                          Not Found   
4463                                          Not Found   
4464                                          Not Found   
4465  C[C@@H]1CC2=C(CCC(=O)C2)[C@@H]3[C@@H]1[C@@H]4C...   

                                                  InChI  \
0     InChI=1S/C27H32F2N8/c1-5-35-8-10-36(11-9-35)16...   
1     InChI=1S/C22H28N2O/c1-2-22(25)24(20-11-7-4-8-1...   
2     InChI=1S/C47H51NO14/c1-25-31(60-43(56)36(52)35...   
3     InChI=1S/C22H28N2O.C18H21NO4.C15H21NO2/c1-2-22...   
4     InChI=1S/C18H25NO/c1-19-10-9-18-8-4-3-5-15(18)...   
...                                                 ...   
4461                                          Not Found   
4462                                          Not Found   
4463                                          Not Found   
4464                                          Not Found   
4465  InChI=1S/C21H28O2/c1-4-21(23)10-8-18-19-13(2)1...   

                         InChIKey  
0     UZWDCWONPYILKI-UHFFFAOYSA-N  
1     PJMPHNIQZUBGLI-UHFFFAOYSA-N  
2     RCINICONZNJXQF-MZXODVADSA-N  
3     BWFZGLIDGVJKML-ACOWMKLESA-N  
4     MKXZASYAUGDDCJ-NJAFHUGGSA-N  
...                           ...  
4461                    Not Found  
4462                    Not Found  
4463                    Not Found  
4464                    Not Found  
4465  WZDGZWOAQTVYBX-XOINTXKNSA-N  

[4466 rows x 5 columns]

In [2]:
fdi_key.to_csv('/Users/raynasser/code/raynasser/MediSure/data/raw_data/FooDru/unique_foods_key.csv')

In [7]:
fdi_key = fdi_key[fdi_key.InChIKey != 'Not Found']
fdi_key

Unnamed: 0.1  Unnamed: 0               drug  \
0                0           0        abemaciclib   
1                1           1           fentanyl   
2                2           2         paclitaxel   
3                3           3  opioid analgesics   
4                4           4   dextromethorphan   
...            ...         ...                ...   
4440          4440        4440       pomalidomide   
4450          4450        4450           cdb-2914   
4452          4452        4452             lupron   
4460          4460        4460          droxidopa   
4465          4465        4465           tibolone   

                                                 SMILES  \
0     CCN1CCN(CC1)CC2=CN=C(C=C2)NC3=NC=C(C(=N3)C4=CC...   
1          CCC(=O)N(C1CCN(CC1)CCC2=CC=CC=C2)C3=CC=CC=C3   
2     CC1=C2[C@H](C(=O)[C@@]3([C@H](C[C@@H]4[C@]([C@...   
3     CCC(=O)N(C1CCN(CC1)CCC2=CC=CC=C2)C3=CC=CC=C3.C...   
4       CN1CC[C@@]23CCCC[C@@H]2[C@@H]1CC4=C3C=C(C=C4)OC   
...                                                 ...   
4440        C1CC(=O)NC(=O)C1N2C(=O)C3=C(C2=O)C(=CC=C3)N   
4450  CC(=O)[C@]1(CC[C@@H]2[C@@]1(C[C@@H](C3=C4CCC(=...   
4452  CCNC(=O)[C@@H]1CCCN1C(=O)[C@H](CCCN=C(N)N)NC(=...   
4460           C1=CC(=C(C=C1[C@H]([C@@H](C(=O)O)N)O)O)O   
4465  C[C@@H]1CC2=C(CCC(=O)C2)[C@@H]3[C@@H]1[C@@H]4C...   

                                                  InChI  \
0     InChI=1S/C27H32F2N8/c1-5-35-8-10-36(11-9-35)16...   
1     InChI=1S/C22H28N2O/c1-2-22(25)24(20-11-7-4-8-1...   
2     InChI=1S/C47H51NO14/c1-25-31(60-43(56)36(52)35...   
3     InChI=1S/C22H28N2O.C18H21NO4.C15H21NO2/c1-2-22...   
4     InChI=1S/C18H25NO/c1-19-10-9-18-8-4-3-5-15(18)...   
...                                                 ...   
4440  InChI=1S/C13H11N3O4/c14-7-3-1-2-6-10(7)13(20)1...   
4450  InChI=1S/C30H37NO4/c1-18(32)30(35-19(2)33)15-1...   
4452  InChI=1S/C59H84N16O12.C2H4O2/c1-6-63-57(86)48-...   
4460  InChI=1S/C9H11NO5/c10-7(9(14)15)8(13)4-1-2-5(1...   
4465  InChI=1S/C21H28O2/c1-4-21(23)10-8-18-19-13(2)1...   

                         InChIKey  
0     UZWDCWONPYILKI-UHFFFAOYSA-N  
1     PJMPHNIQZUBGLI-UHFFFAOYSA-N  
2     RCINICONZNJXQF-MZXODVADSA-N  
3     BWFZGLIDGVJKML-ACOWMKLESA-N  
4     MKXZASYAUGDDCJ-NJAFHUGGSA-N  
...                           ...  
4440  UVSMNLNDYGZFPF-UHFFFAOYSA-N  
4450  OOLLAFOLCSJHRE-ZHAKMVSLSA-N  
4452  RGLRXNKKBLIBQS-XNHQSDQCSA-N  
4460  QXWYKJLNLSIPIN-JGVFFNPUSA-N  
4465  WZDGZWOAQTVYBX-XOINTXKNSA-N  

[1887 rows x 6 columns]

In [10]:
fdi_key.InChIKey.unique()

1670

In [13]:
fdi_key.drop_duplicates(subset='InChIKey', inplace=True)

/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_64663/2744640204.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fdi_key.drop_duplicates(subset='InChIKey', inplace=True)


In [15]:
fdi_key.drop(columns=['Unnamed: 0', 'Unnamed: 0.1'], inplace=True)

/var/folders/qx/yrwdfm5j0jz1gmhp0x2tvjy80000gn/T/ipykernel_64663/2786361030.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fdi_key.drop(columns=['Unnamed: 0', 'Unnamed: 0.1'], inplace=True)


In [17]:
fdi_key.to_csv('/Users/raynasser/code/raynasser/MediSure/data/raw_data/FooDru/unique_foods_key.csv')

In [18]:
key = pd.read_csv('/Users/raynasser/code/raynasser/MediSure/data/raw_data/FooDru/unique_foods_key.csv')
key

Unnamed: 0               drug  \
0              0        abemaciclib   
1              1           fentanyl   
2              2         paclitaxel   
3              3  opioid analgesics   
4              4   dextromethorphan   
...          ...                ...   
1665        4436                ger   
1666        4440       pomalidomide   
1667        4452             lupron   
1668        4460          droxidopa   
1669        4465           tibolone   

                                                 SMILES  \
0     CCN1CCN(CC1)CC2=CN=C(C=C2)NC3=NC=C(C(=N3)C4=CC...   
1          CCC(=O)N(C1CCN(CC1)CCC2=CC=CC=C2)C3=CC=CC=C3   
2     CC1=C2[C@H](C(=O)[C@@]3([C@H](C[C@@H]4[C@]([C@...   
3     CCC(=O)N(C1CCN(CC1)CCC2=CC=CC=C2)C3=CC=CC=C3.C...   
4       CN1CC[C@@]23CCCC[C@@H]2[C@@H]1CC4=C3C=C(C=C4)OC   
...                                                 ...   
1665     C(CC(C(=O)O)NC(=O)C(CCC(=O)O)NC(=O)CN)CN=C(N)N   
1666        C1CC(=O)NC(=O)C1N2C(=O)C3=C(C2=O)C(=CC=C3)N   
1667  CCNC(=O)[C@@H]1CCCN1C(=O)[C@H](CCCN=C(N)N)NC(=...   
1668           C1=CC(=C(C=C1[C@H]([C@@H](C(=O)O)N)O)O)O   
1669  C[C@@H]1CC2=C(CCC(=O)C2)[C@@H]3[C@@H]1[C@@H]4C...   

                                                  InChI  \
0     InChI=1S/C27H32F2N8/c1-5-35-8-10-36(11-9-35)16...   
1     InChI=1S/C22H28N2O/c1-2-22(25)24(20-11-7-4-8-1...   
2     InChI=1S/C47H51NO14/c1-25-31(60-43(56)36(52)35...   
3     InChI=1S/C22H28N2O.C18H21NO4.C15H21NO2/c1-2-22...   
4     InChI=1S/C18H25NO/c1-19-10-9-18-8-4-3-5-15(18)...   
...                                                 ...   
1665  InChI=1S/C13H24N6O6/c14-6-9(20)18-7(3-4-10(21)...   
1666  InChI=1S/C13H11N3O4/c14-7-3-1-2-6-10(7)13(20)1...   
1667  InChI=1S/C59H84N16O12.C2H4O2/c1-6-63-57(86)48-...   
1668  InChI=1S/C9H11NO5/c10-7(9(14)15)8(13)4-1-2-5(1...   
1669  InChI=1S/C21H28O2/c1-4-21(23)10-8-18-19-13(2)1...   

                         InChIKey  
0     UZWDCWONPYILKI-UHFFFAOYSA-N  
1     PJMPHNIQZUBGLI-UHFFFAOYSA-N  
2     RCINICONZNJXQF-MZXODVADSA-N  
3     BWFZGLIDGVJKML-ACOWMKLESA-N  
4     MKXZASYAUGDDCJ-NJAFHUGGSA-N  
...                           ...  
1665  DHDOADIPGZTAHT-UHFFFAOYSA-N  
1666  UVSMNLNDYGZFPF-UHFFFAOYSA-N  
1667  RGLRXNKKBLIBQS-XNHQSDQCSA-N  
1668  QXWYKJLNLSIPIN-JGVFFNPUSA-N  
1669  WZDGZWOAQTVYBX-XOINTXKNSA-N  

[1670 rows x 5 columns]